In [1]:
# setup needed Py packages:
import numpy as np
from scipy.optimize import differential_evolution as DE
import win32com.client

In [2]:
# Instantiate the main OpenDSS Object:
try:
    dssObj = win32com.client.Dispatch("OpenDSSengine.DSS")
except:
    print ("Unable to start the OpenDSS Engine")
    raise SystemExit

In [3]:
# Instantiate the other OpenDSS Object:
dssText = dssObj.Text  # Definiranje tekstualnog objekta
dssCircuit = dssObj.ActiveCircuit  # Definiranje objekta mreze
dssSolution = dssCircuit.Solution  # Definiranje objekta rjesenja
dssElem = dssCircuit.ActiveCktElement  # Definiranje objekta elementa mreze

In [5]:
# Compail the OpenDSS file
#dssText.Command = r"Compile 'C:\Users\mimit1\Documents\OpenDSS\Exercise3dss.dss'"
dssText.Command = r"Compile 'C:\Users\Barukcic\Documents\OpenDSS\Exercise3dss.dss'"

In [6]:
# Get node names:
NodeN = dssCircuit.AllNodeNames
# and print them:
print (NodeN)

('sour.1', 'sour.2', 'sour.3', 'b2.1', 'b2.2', 'b2.3', 'b3.1', 'b3.2', 'b3.3', 'b4.1', 'b4.2', 'b4.3', 'b5.1', 'b5.2', 'b5.3', 'b6.1', 'b6.2', 'b6.3', 'b7.1', 'b7.2', 'b7.3', 'b8.1', 'b8.2', 'b8.3', 'b9.1', 'b9.2', 'b9.3', 'b10.1', 'b10.2', 'b10.3', 'b11.1', 'b11.2', 'b11.3', 'b12.1', 'b12.2', 'b12.3', 'b13.1', 'b13.2', 'b13.3', 'b14.1', 'b14.2', 'b14.3', 'b15.1', 'b15.2', 'b15.3', 'b16.1', 'b16.2', 'b16.3', 'b17.1', 'b17.2', 'b17.3', 'b18.1', 'b18.2', 'b18.3', 'b19.1', 'b19.2', 'b19.3', 'b20.1', 'b20.2', 'b20.3', 'b21.1', 'b21.2', 'b21.3', 'b22.1', 'b22.2', 'b22.3', 'b23.1', 'b23.2', 'b23.3', 'b24.1', 'b24.2', 'b24.3', 'b25.1', 'b25.2', 'b25.3', 'b26.1', 'b26.2', 'b26.3', 'b27.1', 'b27.2', 'b27.3', 'b28.1', 'b28.2', 'b28.3', 'b29.1', 'b29.2', 'b29.3', 'b30.1', 'b30.2', 'b30.3', 'b31.1', 'b31.2', 'b31.3', 'b32.1', 'b32.2', 'b32.3', 'b33.1', 'b33.2', 'b33.3', 'b34.1', 'b34.2', 'b34.3')


In [7]:
# Repeat for bus names:
BusN = dssCircuit.AllBusNames
print (BusN)

('sour', 'b2', 'b3', 'b4', 'b5', 'b6', 'b7', 'b8', 'b9', 'b10', 'b11', 'b12', 'b13', 'b14', 'b15', 'b16', 'b17', 'b18', 'b19', 'b20', 'b21', 'b22', 'b23', 'b24', 'b25', 'b26', 'b27', 'b28', 'b29', 'b30', 'b31', 'b32', 'b33', 'b34')


In [8]:
# Get some properties of the load element:
dssCircuit.Loads.Name = 'L2'
VL2 = dssCircuit.Loads.kV
PL2 = dssCircuit.Loads.kW
QL2 = dssCircuit.Loads.kvar
# and print them:
print ('Nominal voltage of load L2 is: ', VL2, 'kV \n',
       'Nominal active power of L2 is: ', PL2, 'kW \n',
       'Nominal reactive power of L2 is: ', QL2, 'kvar \n',
       'and complex power of L2 is: ', complex(PL2, QL2), 'kVA')

Nominal voltage of load L2 is:  11.0 kV 
 Nominal active power of L2 is:  230.0 kW 
 Nominal reactive power of L2 is:  142.5 kvar 
 and complex power of L2 is:  (230+142.5j) kVA


In [10]:
# Get nominal loads:
LNP = []
LNQ = []
load = dssCircuit.Loads
Li = load.First 
nL=0
while Li:     
    LNP.append(load.kW)
    LNQ.append(load.kVAR)
    nL +=1
    Li = load.Next

# print nominal loads:
print ('Nominal loads are, PL: ',LNP,
      '\n and QL: ', LNQ)

Nominal loads are, PL:  [230.0, 0.0, 230.0, 230.0, 0.0, 0.0, 230.0, 230.0, 0.0, 230.0, 137.0, 72.0, 72.0, 72.0, 13.5, 230.0, 230.0, 230.0, 230.0, 230.0, 230.0, 230.0, 230.0, 230.0, 230.0, 137.0, 75.0, 75.0, 75.0, 57.0, 57.0, 57.0, 57.0] 
 and QL:  [142.5, 0.0, 142.5, 142.5, 0.0, 0.0, 142.5, 142.5, 0.0, 142.5, 84.0, 45.0, 45.0, 45.0, 7.5, 142.5, 142.5, 142.5, 142.5, 142.5, 142.5, 142.5, 142.5, 142.5, 142.5, 85.0, 48.0, 48.0, 48.0, 34.5, 34.5, 34.5, 34.5]


In [30]:
# Let's make the objective function of the optimization problem of optimal allocation of DG in the distribution network in form of PY function:
def FC(ind, *addtnP):
    # decoding DG allocation from DE individual
    LOCdg = int(round(ind[0]))  # decode DG location from DE individual
    # print (type(LOCdg)) - control line
    Pdg = ind[1]  # decode DG powers from DE individual
    Qdg = ind[2]
    
    # change DG location and power in OpenDSS script:
    dssText.Command = 'Edit generator.DG' + ' bus1=' + BusN[LOCdg] + ' kw=' + str(Pdg) + ' kvar=' + str(Qdg)

    # execute simulation with changed DG location and powers for each part of load shape curve:
    EL = [] # initilzation of energy loss list
    VmaxV = [] # initilzation of maximum voltage list
    VminV = [] # initilzation of minimum voltage list
    for ij in range(len(PL)):
        load = dssCircuit.Loads
        Li = load.First 
        nL=0
        while Li:     
            load.kW = PL[ij] * LNP[nL]
            load.kvar = PL[ij] * LNQ[nL]
            nL +=1
            Li = load.Next
        dssSolution.Solve()
        # get nodal voltages, maximum and minimum voltages in [p.u]
        Vpu = dssCircuit.AllBusVmagPU
        Vmax = max(Vpu)
        Vmin = min(Vpu)
        VmaxV.append(Vmax)
        VminV.append(Vmin)
        # get network loosses
        NL = dssCircuit.Losses[0]/1000  # divide by 1000 to get numerical value in [kW]
        # check inequality constraints and penalize OF if they not satisfied (soft penalisation):
        if Vmax > Vu:
            NL = 2*(1+Vmax-Vu)*NL # increased penalisation by factor 2
        if Vmin < Vl:
            NL = 2*(1+Vl-Vmin)*NL
        EL.append(NL*TL[ij]) # get energy losses for ij-th load level in duration of ij-th period in [kWh]
    # use network losses as objective function value
    return EL, VminV, VmaxV

def OF(ind, *addtnP):
    FNC = FC(ind, *addtnP)
    return sum(FNC[0]) # total daily energy losses

In [31]:
# set voltage limits in [p.u] (inequality constraints)
Vl = 0.9
Vu = 1.1

# define load shape: load power and time duration in form of Python list:
PL = [0.4, 0.8, 1.0]
TL = [8, 6, 10]

# and forward them as additional parameters of objective function (together with nominal loads)
addtnP = (Vl, Vu, PL, TL, LNP, LNQ)

In [32]:
# Control cell, check if objective function work well
indp = [9.8, 500.0, 350.0]
NLp = OF(indp, addtnP)
NLpp = FC(indp, addtnP)

# total network losses are:
print ('Active network losses are: ', NLp, '[kWh]')
print ('Active network losses, min and max voltages are: ', NLpp, '[kW, p.u., p.u.]')

Active network losses are:  2557.5520849898053 [kWh]
Active network losses, min and max voltages are:  ([166.08644709898854, 634.7292304204398, 1756.736407470377], [0.980343250929517, 0.9560131126610388, 0.9437487446524763], [0.9994445497306317, 0.9986372653413943, 0.9982302096374378]) [kW, p.u., p.u.]


In [33]:
# define optimization part: (tip: see the notebook you made in exercise 1)
# Power limits of DG
PDGmin = 0.0
PDGmax = 5000.0
QDGmin = -2000.0
QDGmax = 2000.0

# define box constraints (decision variable ranges (limits))
BXC = [(0.0, len(BusN)-0.6),
      (PDGmin, PDGmax),
      (QDGmin, QDGmax)] # 0 - 1000 kW
print (BXC)

[(0.0, 33.4), (0.0, 5000.0), (-2000.0, 2000.0)]


In [37]:
# performe optimization by using DE
solution = DE(OF, BXC, addtnP, maxiter=500, popsize=200, mutation=(0.5, 1), recombination=0.7, disp=False, polish=False, tol=0.001)
print ('##################################################### \n', solution, '\n ##################################################### \n')
print ('\n','Problem solution is: ', solution.x, '\n', ', and total network lossess are: ', solution.fun, 'kW',
      '\n for optimal allocation: ', 
       '\n DG location in bus: ', BusN[int(round(solution.x[0]))],
      '\n injecting active power of : ', solution.x[1], 'kW',
      '\n and rective power of : ', solution.x[2], 'kvar',)
print ('\n Minimal and maximal nodal voltages are: ', FC(solution.x, addtnP)[1], ' and ', FC(solution.x, addtnP)[2])

##################################################### 
      fun: 964.5369190867824
 message: 'Optimization terminated successfully.'
    nfev: 12000
     nit: 19
 success: True
       x: array([  19.92646986, 2217.46909805, 1358.77310326]) 
 ##################################################### 


 Problem solution is:  [  19.92646986 2217.46909805 1358.77310326] 
 , and total network lossess are:  964.5369190867824 kW 
 for optimal allocation:  
 DG location in bus:  b21 
 injecting active power of :  2217.4690980530677 kW 
 and rective power of :  1358.7731032604463 kvar

 Minimal and maximal nodal voltages are:  [1.00014167817882, 0.9849445585628107, 0.9769826293088005]  and  [1.0163383827716714, 0.9993577518685043, 0.9989585187008927]


In [39]:
# get losses for different load levels:
print ('\n Energy losses for different load levels are: ', FC(solution.x, addtnP)[0])
print ('\n and power losses for different load levels are: ', [FC(solution.x, addtnP)[0][iL]/TL[iL] for iL in range(len(PL))])


 Energy losses for different load levels are:  [218.0279801321201, 180.93571217174804, 565.5781826046511]

 and power losses for different load levels are:  [27.25349751651501, 30.15595202862467, 56.55781826046511]
